# Supported data libraries

In [ ]:
# hidden on the website
import numpy as np

np.random.seed(1)

The `.hvplot()` [plotting API](api-plotting) supports a wide range of data sources. For most of them, a special import can be executed to register the `.hvplot` accessor on specific objects. For instance, importing `hvplot.pandas` registers the `.hvplot` accessor on Pandas `DataFrame` and `Series` objects, allowing to call `df.hvplot.line()`.

Among the data sources introduced below, [Pandas](https://pandas.pydata.org) is the only library that doesn't need to be installed separately as it is a direct dependency of hvPlot.

The following table provides a summary of the data sources supported by hvPlot. The *HoloViews interface* column indicates whether HoloViews offers [an interface](inv:holoviews#holoviews.core.data) for that data source, meaning the data would in most cases not be converted to another type until the very last steps of the rendering process. When no interface is available for a data type, hvPlot internally casts the data to a supported type, for instance `polars` objects are casted upfront to `pandas` objects.

| Source                            | Module           | Type              | HoloViews interface | Comment                       |
| --------------------------------- | ---------------- | ----------------- | ------------------- | ----------------------------- |
| [Pandas](#libraries-pandas)       | `hvplot.pandas`  | Tabular           | ✅                  |                               |
| [Dask](#libraries-dask)           | `hvplot.dask`    | Tabular           | ✅                  |                               |
| [Geopandas](#libraries-geopandas) | `hvplot.pandas`  | Tabular           | ✅                  |                               |
| [Ibis](#libraries-ibis)           | `hvplot.ibis`    | Tabular           | ✅                  |                               |
| [Polars](#libraries-polars)       | `hvplot.polars`  | Tabular           | ❌                  | To Pandas                     |
| [DuckDB](#libraries-duckdb)       | `hvplot.duckdb`  | Tabular           | ❌                  | To Pandas                     |
| [RAPIDS cuDF](#libraries-cudf)    | `hvplot.cudf`    | Tabular           | ✅                  | GPU                           |
| [Fugue](#libraries-fugue)         | `hvplot.fugue`   | Tabular           | ❌                  | Experimental                  |
| [Xarray](#libraries-xarray)       | `hvplot.xarray`  | Multidimensional | ✅                  |                               |
| [Intake](#libraries-intake)       | `hvplot.intake`  | Catalog           | ❌                  |                               |
| [Streamz](#libraries-streamz)     | `hvplot.streamz` | Streaming         | ✅                  |                               |
| [NetworkX](#libraries-networkx)   | -                | Graph             | -                   | [Different API](api-networkx) |


:::{note}
Supporting so many data sources is hard work! We are aware that the support for some of them isn't as good as we would like. If you encounter any issue please report it <a href='https://github.com/holoviz/hvplot/'>on GitHub</a>, we always welcome Pull Requests too!
:::

## Columnar/tabular

(libraries-pandas)=
### Pandas

`.hvplot()` supports [Pandas](https://pandas.pydata.org) `DataFrame` and `Series` objects. hvPlot can also be registered as Pandas' default plotting backend to delegate Pandas `.plot()` calls to hvPlot directly instead of to Pandas' Matplotlib backend. Find out more about [hvPlot's compatibility with Pandas' plotting interface](./api_compatibility/pandas/index.ipynb).

In [ ]:
import hvplot.pandas  # noqa
import pandas as pd

df_pandas = pd.DataFrame(np.random.randn(1000, 4), columns=list('ABCD')).cumsum()
df_pandas.head(2)

In [ ]:
# Pandas DataFrame
df_pandas.hvplot.line(height=150)

In [ ]:
# Pandas Series
s_pandas = df_pandas['A']
s_pandas.hvplot.line(height=150)

(libraries-dask)=
### [Dask](https://www.dask.org)

`.hvplot()` supports [Dask](https://www.dask.org) `DataFrame` and `Series` objects.

In [ ]:
import hvplot.dask  # noqa
import dask

df_dask = dask.dataframe.from_pandas(df_pandas, npartitions=2)
df_dask

In [ ]:
# Dask DataFrame
df_dask.hvplot.line(height=150)

In [ ]:
# Dask Series
s_dask = df_dask['A']
s_dask.hvplot.line(height=150)

(libraries-geopandas)=
### GeoPandas

`.hvplot()` supports [GeoPandas](https://geopandas.org) `GeoDataFrame` objects.

In [ ]:
import hvplot.pandas  # noqa
import geopandas as gpd

p_geometry = gpd.points_from_xy(
    x=[12.45339, 12.44177, 9.51667, 6.13000],
    y=[41.90328, 43.93610, 47.13372, 49.61166],
    crs='EPSG:4326'
)
p_names = ['Vatican City', 'San Marino', 'Vaduz', 'Luxembourg']
gdf = gpd.GeoDataFrame(dict(name=p_names), geometry=p_geometry)
gdf.head(2)

In [ ]:
# GeoPandas GeoDataFrame
gdf.hvplot.points(geo=True, tiles='CartoLight', frame_height=150, data_aspect=0.5)

(libraries-ibis)=
### Ibis

[Ibis](https://ibis-project.org/) is the "portable Python dataframe library", it provides a unified interface to many data backends (e.g. DuckDB, SQLite, SnowFlake, Google BigQuery). `.hvplot()` supports [Ibis](https://ibis-project.org/) `Expr` objects.

In [ ]:
import hvplot.ibis  # noqa
import ibis

table = ibis.memtable(df_pandas.reset_index())
table

In [ ]:
# Ibis Expr
table.hvplot.line(x='index', height=150)

(libraries-polars)=
### Polars

:::{note}
Added in version `0.9.0`.
:::

:::{important}
While other data sources like `Pandas` or `Dask` have built-in support in HoloViews, as of version 1.17.1 this is not yet the case for `Polars`. You can track this [issue](https://github.com/holoviz/holoviews/issues/5939) to follow the evolution of this feature in HoloViews. Internally hvPlot simply selects the columns that contribute to the plot and casts them to a Pandas object using Polars' `.to_pandas()` method.
:::

In [ ]:
import hvplot.polars  # noqa 
import polars

df_polars = polars.from_pandas(df_pandas)
df_polars.head(2)

`.hvplot()` supports [Polars](https://www.pola.rs/) `DataFrame`, `LazyFrame` and `Series` objects.

In [ ]:
# Polars DataFrame
df_polars.hvplot.line(y=['A', 'B', 'C', 'D'], height=150)

In [ ]:
# Polars LazyFrame
df_polars.lazy().hvplot.line(y=['A', 'B', 'C', 'D'], height=150)

In [ ]:
# Polars Series
df_polars['A'].hvplot.line(height=150)

(libraries-duckdb)=
### DuckDB

:::{note}
Added in version `0.11.0`.
:::

In [ ]:
import numpy as np
import pandas as pd

df_pandas = pd.DataFrame(np.random.randn(1000, 4), columns=list('ABCD')).cumsum()
df_pandas.head(2)

In [ ]:
import hvplot.duckdb  # noqa 
import duckdb

connection = duckdb.connect(':memory:')
relation = duckdb.from_df(df_pandas, connection=connection)
relation.to_view("example_view");

`.hvplot()` supports [DuckDB](https://duckdb.org/docs/api/python/overview.html) `DuckDBPyRelation` and `DuckDBConnection` objects.

In [ ]:
relation.hvplot.line(y=['A', 'B', 'C', 'D'], height=150)

`DuckDBPyRelation` is a bit more optimized because it handles column subsetting directly within DuckDB before the data is converted to a `pd.DataFrame`.

So, it's a good idea to use the `connection.sql()` method when possible, which gives you a `DuckDBPyRelation`, instead of `connection.execute()`, which returns a `DuckDBPyConnection`.

In [ ]:
sql_expr = "SELECT * FROM example_view WHERE A > 0 AND B > 0"
connection.sql(sql_expr).hvplot.line(y=['A', 'B'], hover_cols=["C"], height=150)  # subsets A, B, C

Alternatively, you can directly subset the desired columns in the SQL expression.

In [ ]:
sql_expr = "SELECT A, B, C FROM example_view WHERE A > 0 AND B > 0"
connection.execute(sql_expr).hvplot.line(y=['A', 'B'], hover_cols=["C"], height=150)

(libraries-cudf)=
### Rapids cuDF

:::{important}
[Rapids cuDF](https://docs.rapids.ai/api/cudf) is a Python **GPU** DataFrame library. Neither hvPlot's nor HoloViews' test suites currently run on a GPU part of their CI, as of versions 0.9.0 and 1.17.1, respectively. This is due to the non availability of machines equipped with a GPU on the free CI system we rely on (Github Actions). Therefore it's possible that support for cuDF gets degraded in hvPlot without us noticing it immediately. Please report any issue you might encounter.
:::

`.hvplot()` supports [cuDF](https://docs.rapids.ai/api/cudf) `DataFrame` and `Series` objects.

(libraries-fugue)=
### Fugue

:::{admonition} Experimental
:class: caution
[Fugue](https://fugue-tutorials.readthedocs.io/) support, added in version `0.9.0`, is experimental and may change in future versions.
:::

hvPlot adds the `hvplot` plotting extension to FugueSQL.

In [ ]:
import hvplot.fugue  # noqa
import fugue

fugue.api.fugue_sql(
    """
    OUTPUT df_pandas USING hvplot:line(
        height=150,
    )
    """
)

## Multidimensional

(libraries-xarray)=
### Xarray

`.hvplot()` supports [XArray](https://xarray.pydata.org) `Dataset` and `DataArray` labelled multidimensional objects.

In [ ]:
import hvplot.xarray  # noqa
import xarray as xr

ds = xr.Dataset({
    'A': (['x', 'y'], np.random.randn(100, 100)),
    'B': (['x', 'y'], np.random.randn(100, 100))},
    coords={'x': np.arange(100), 'y': np.arange(100)}
)
ds

In [ ]:
# Xarray Dataset
ds.hvplot.hist(height=150)

In [ ]:
# Xarray DataArray
ds['A'].hvplot.image(height=150)

## Catalog

(libraries-intake)=
### Intake

`.hvplot()` supports [Intake](https://github.com/intake/intake) `DataSource` objects.

## Streaming

(libraries-streamz)=
### Streamz

`.hvplot()` supports [Streamz](https://streamz.readthedocs.io) `DataFrame`, `DataFrames`, `Series` and `Seriess` objects.

## Graph

(libraries-networkx)=
### NetworkX

The hvPlot [NetworkX](https://networkx.github.io) plotting API is meant as a drop-in replacement for the `networkx.draw` methods. The `draw` and other `draw_<>` methods are available in the `hvplot.networkx` module.

In [ ]:
import hvplot.networkx as hvnx
import networkx as nx

G = nx.petersen_graph()
hvnx.draw(G, with_labels=True, height=150)